In [19]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/mnist-png/mnist_png/training/7/52235.png
/kaggle/input/mnist-png/mnist_png/training/7/9273.png
/kaggle/input/mnist-png/mnist_png/training/7/18966.png
/kaggle/input/mnist-png/mnist_png/training/7/45170.png
/kaggle/input/mnist-png/mnist_png/training/7/4353.png
/kaggle/input/mnist-png/mnist_png/training/7/41461.png
/kaggle/input/mnist-png/mnist_png/training/7/49472.png
/kaggle/input/mnist-png/mnist_png/training/7/26801.png
/kaggle/input/mnist-png/mnist_png/training/7/32197.png
/kaggle/input/mnist-png/mnist_png/training/7/59254.png
/kaggle/input/mnist-png/mnist_png/training/7/41414.png
/kaggle/input/mnist-png/mnist_png/training/7/57325.png
/kaggle/input/mnist-png/mnist_png/training/7/18315.png
/kaggle/input/mnist-png/mnist_png/training/7/23000.png
/kaggle/input/mnist-png/mnist_png/training/7/22739.png
/kaggle/input/mnist-png/mnist_png/training/7/1231.png
/kaggle/input/mnist-png/mnist_png/training/7/58383.png
/kaggle/input/mnist-png/mnist_png/training/7/23621.png
/kaggle/input

In [20]:
import torch
from torch.utils.data import Dataset
import os
import pandas as pd
from torchvision.io import read_image
from torchvision.transforms import v2
from torch.utils.data import DataLoader
from torch import nn

In [21]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cuda', index=0)

In [22]:
torch.cuda.device_count()

1

In [23]:
learning_rate = 1e-3
batch_size = 128
epochs = 20

In [24]:
class CustomImageDataset(Dataset):
    def __init__(self, annotations_file, img_dir, transform=None, target_transform=None):
        self.img_labels = pd.read_csv(annotations_file)
        self.img_dir = img_dir
        self.transform = transform
        self.target_transform = target_transform

    def __len__(self):
        return len(self.img_labels)

    def __getitem__(self, idx):
        label = self.img_labels.iloc[idx, 1]
        img_path = os.path.join(self.img_dir, str(label), self.img_labels.iloc[idx, 0])
        image = read_image(img_path)
        
        if self.transform:
            image = self.transform(image)
        if self.target_transform:
            label = self.target_transform(label)
        return image, label

In [25]:
train_img_dir = "/kaggle/input/mnist-png/mnist_png/training"
label_folders = os.listdir(train_img_dir)
full_train_df = pd.DataFrame()
for folder in label_folders:
    image_names = os.listdir(os.path.join(train_img_dir, folder))
    image_labels = [folder for i in range(len(image_names))]
    df = pd.DataFrame([image_names, image_labels]).transpose()
    full_train_df = pd.concat([full_train_df, df], axis = 0)
full_train_df.to_csv("train_images.csv", index = False)

In [26]:
train_annotations_file = "/kaggle/working/train_images.csv"

In [27]:
transforms = v2.Compose([
    v2.RandomResizedCrop(size=(22, 22), antialias=True),
    v2.RandomHorizontalFlip(p=0.5),
    v2.ToDtype(torch.float32, scale = True),
])

In [28]:
train_dataset = CustomImageDataset(train_annotations_file, train_img_dir, transforms)

In [29]:
test_img_dir = "/kaggle/input/mnist-png/mnist_png/testing"
label_folders = os.listdir(test_img_dir)
full_test_df = pd.DataFrame()
for folder in label_folders:
    image_names = os.listdir(os.path.join(test_img_dir, folder))
    image_labels = [folder for i in range(len(image_names))]
    df = pd.DataFrame([image_names, image_labels]).transpose()
    full_test_df = pd.concat([full_test_df, df], axis = 0)
full_test_df.to_csv("test_images.csv", index = False)

In [30]:
test_annotations_file = "/kaggle/working/test_images.csv"

In [31]:
test_dataset = CustomImageDataset(test_annotations_file, test_img_dir, transforms)

In [32]:
train_dataloader = DataLoader(train_dataset, batch_size= batch_size, shuffle=True)
test_dataloader = DataLoader(test_dataset, batch_size= batch_size, shuffle=True)

In [33]:
train_features, train_labels = next(iter(train_dataloader))
print(f"Feature batch shape: {train_features.size()}")
print(f"Labels batch shape: {train_labels.size()}")

Feature batch shape: torch.Size([128, 1, 22, 22])
Labels batch shape: torch.Size([128])


In [34]:
class NeuralNetwork(nn.Module):
    def __init__(self):
        super().__init__()
        self.flatten = nn.Flatten()
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(22*22, 1024),
            nn.ReLU(),
            nn.Linear(1024, 512),
            nn.ReLU(),
            nn.Linear(512, 256),
            nn.ReLU(),
            nn.Linear(256, 128),
            nn.ReLU(),
            nn.Linear(128, 10),
        )

    def forward(self, x):
        x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits

In [35]:
model = NeuralNetwork().to(device)
print(model)

NeuralNetwork(
  (flatten): Flatten(start_dim=1, end_dim=-1)
  (linear_relu_stack): Sequential(
    (0): Linear(in_features=484, out_features=1024, bias=True)
    (1): ReLU()
    (2): Linear(in_features=1024, out_features=512, bias=True)
    (3): ReLU()
    (4): Linear(in_features=512, out_features=256, bias=True)
    (5): ReLU()
    (6): Linear(in_features=256, out_features=128, bias=True)
    (7): ReLU()
    (8): Linear(in_features=128, out_features=10, bias=True)
  )
)


In [36]:
loss_fn = nn.CrossEntropyLoss().to(device)
optimizer = torch.optim.SGD(model.parameters(), lr=learning_rate)

In [37]:
def train_loop(dataloader, model, loss_fn, optimizer):
    size = len(dataloader.dataset)
    # Set the model to training mode - important for batch normalization and dropout layers
    # Unnecessary in this situation but added for best practices
    model.train()
    for batch, (X, y) in enumerate(dataloader):
        # Compute prediction and loss
        pred = model(X.to(device))
        loss = loss_fn(pred, y.to(device))

        # Backpropagation
        loss.backward()
        optimizer.step()
        optimizer.zero_grad()

        if batch % 100 == 0:
            loss, current = loss.item(), batch * batch_size + len(X)
            print(f"loss: {loss:>7f}  [{current:>5d}/{size:>5d}]")


def test_loop(dataloader, model, loss_fn):
    # Set the model to evaluation mode - important for batch normalization and dropout layers
    # Unnecessary in this situation but added for best practices
    model.eval()
    size = len(dataloader.dataset)
    num_batches = len(dataloader)
    test_loss, correct = 0, 0

    # Evaluating the model with torch.no_grad() ensures that no gradients are computed during test mode
    # also serves to reduce unnecessary gradient computations and memory usage for tensors with requires_grad=True
    with torch.no_grad():
        for X, y in dataloader:
            pred = model(X.to(device))
            test_loss += loss_fn(pred, y.to(device)).item()
            correct += (pred.argmax(1) == y.to(device)).type(torch.float).sum().item()

    test_loss /= num_batches
    correct /= size
    print(f"Test Error: \n Accuracy: {(100*correct):>0.1f}%, Avg loss: {test_loss:>8f} \n")

In [38]:
for t in range(epochs):
    print(f"Epoch {t+1}\n-------------------------------")
    train_loop(train_dataloader, model, loss_fn, optimizer)
    test_loop(test_dataloader, model, loss_fn)
print("Done!")

Epoch 1
-------------------------------
loss: 2.304477  [  128/60000]
loss: 2.307641  [12928/60000]
loss: 2.310675  [25728/60000]
loss: 2.303135  [38528/60000]
loss: 2.309267  [51328/60000]
Test Error: 
 Accuracy: 9.7%, Avg loss: 2.304237 

Epoch 2
-------------------------------
loss: 2.307743  [  128/60000]
loss: 2.299797  [12928/60000]
loss: 2.305254  [25728/60000]
loss: 2.306502  [38528/60000]
loss: 2.307462  [51328/60000]
Test Error: 
 Accuracy: 10.3%, Avg loss: 2.303490 

Epoch 3
-------------------------------
loss: 2.304586  [  128/60000]
loss: 2.298132  [12928/60000]
loss: 2.303907  [25728/60000]
loss: 2.304377  [38528/60000]
loss: 2.298813  [51328/60000]
Test Error: 
 Accuracy: 10.5%, Avg loss: 2.303364 

Epoch 4
-------------------------------
loss: 2.304191  [  128/60000]
loss: 2.296884  [12928/60000]
loss: 2.299230  [25728/60000]
loss: 2.303077  [38528/60000]
loss: 2.308546  [51328/60000]
Test Error: 
 Accuracy: 11.1%, Avg loss: 2.302528 

Epoch 5
-------------------------

In [39]:
torch.save(model, 'model.pth')
#model1 = torch.load('model.pth', weights_only=False),

In [40]:
torch.save(model.state_dict(), 'model_weights.pth')

In [41]:
file_size_bytes =  os.path.getsize('model.pth')

# Convert to MB
file_size_mb = file_size_bytes / (1024 * 1024)

print(f"Model size: {file_size_mb:.3f} MB")

Model size: 4.533 MB


In [42]:
file_size_bytes =  os.path.getsize('model_weights.pth')

# Convert to MB
file_size_mb = file_size_bytes / (1024 * 1024)

print(f"Model state dictionary size: {file_size_mb:.3f} MB")

Model state dictionary size: 4.532 MB
